In [1]:
import sqlite3
import os.path
import hashlib
import pandas as pd
import numpy as np

In [2]:
# select db
db = './test.db'
# db = './../data/daf06fb3ab69f27bd681a63311722181.db'
# db = './../data/a920861bb3f76b973d6bb7fb4d9be5b4.db'

# connect
conn = sqlite3.connect(db)

# create loadsonly view
c = conn.cursor()
c.execute('''DROP VIEW loadsonly''')
c.execute('''CREATE VIEW loadsonly(datetime,demand) AS SELECT date,demand_power FROM loads''')

conn.commit()

# read the data
df = pd.read_sql_query("SELECT * FROM loadsonly;", conn)
df['datetime'] = pd.to_datetime(df['datetime'])
df.sort_values(by='datetime',ascending=True);

# close db
conn.close()


In [3]:
df['dp'] = df['demand'] - df['demand'].shift(1)
df['dp+'] = [0-x if x <=0 else 0 for x in df['dp']]
df['dp-'] = [x if x >=0 else 0 for x in df['dp']]

df['dp'] = df['demand'] - df['demand'].shift(1)
for x in range(1,len(df)):
#     df.loc[x,'dp'] = df.loc[x,'demand'] -  df.loc[x-1,'demand']
    if df.loc[x,'dp'] > 0:
        df.loc[x,'dp+'] = df.loc[x,'dp']
        df.loc[x,'dp-'] = 0
    else:
        df.loc[x,'dp-'] = 0-df.loc[x,'dp']
        df.loc[x,'dp+'] = 0

In [4]:
# add user defined loads
user_loads = {'modem':10,'rPi':4}
baseload = 0
for user_load in user_loads:
    df.loc[:,user_load]  = user_loads[user_load]
    baseload = baseload + user_loads[user_load]
#     df.loc[:,] = np.array([df['demand'].min()] * len(df))


In [5]:
# find baseload and determine remaining unkwown profile
df.loc[:,'baseload'] = np.array([df['demand'].min()-baseload] * len(df))
df.loc[:,'unknown'] = df.loc[:,'demand'] - df.loc[:,'baseload']-baseload


In [6]:
# df[pd.isnull(df).any(axis=1)]

In [7]:
def left_round(number,precision=2):
    rem = number

    d = len(str(number))
    while(round(rem,d) == round(number,d)):
        rem = round(number,d-precision)
        d = d -1
        
    i = 0
    while(rem > 10**precision):
        rem = round(rem / 10,0)
        i = i +1
#         print(rem*(10**i))
        if i > 100:
            break
    return rem*(10**i)

left_round(00.00034564,3)

left_round(122431234.00034564,3)

# left_round(123456)

122000000.0

In [8]:
#find square loads
loads = dict()

for x in range(1,len(df)):
    #filter for dP+ with minimim power
    if df.loc[x,'dp+'] > 100:
        print(' ') #new line in output
        print ('start dp>100:',df.loc[x,'datetime'],'start P:',df.loc[x-1,'unknown'],'dP+:' ,df.loc[x,'dp+'])
        
        #look forwar in time to see how long load remains on
        for y in range(x+1,len(df)):
            #find dP- of same/simulair size 
            if df.loc[y,'dp-'] > 0.9 *df.loc[x,'dp+'] and df.loc[y,'dp-'] < 1.1 *df.loc[x,'dp+']:
                print ('stop dP-:',df.loc[y,'datetime'],'dP-:' ,df.loc[y,'dp-'])
                break
            # check if does not drop below start power (this means is must have been turned of)    
            if df.loc[y,'unknown'] <= df.loc[x-1,'unknown']:
                print ('stop demand:',df.loc[x,'datetime'] ,df.loc[y,'unknown'], ' <= ',df.loc[x-1,'unknown'])
                break
        
        print(x,y,(df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).mean())
        
        # calculate key parameters
        mean = (df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).mean()
        max = (df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).max()
        min = (df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).min()
        std = (df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).std()
        time = pd.Timedelta(pd.to_datetime(df['datetime'][y])-pd.to_datetime(df['datetime'][x]))
        noise = df.loc[x:y-1,'dp'].abs().mean()
        
        print('mean load:',mean)
        print('max load:',max)
        print('std load:',std)
        print('noise:',noise)
        print('time past:',time)


        print('found profile from ',df.loc[x-1,'datetime'],'to',df.loc[y,'datetime'])
        profile = list(df.loc[x-1:y,'unknown']-df.loc[x-1,'unknown'])
        print(profile)
        
        
#         plt.plot(range(x,y),profile)
#         plt.title('A simple chirp')
#         plt.show()
#         break
        try:
            #drop loads which do not have a square looking profile.
            if (std/mean > 0.1):
                print('dropped because of large std:',std/mean)
                continue

            #drop loads which do not have odd start compared to mean
            if( abs(mean-df.loc[x,'dp+'])/df.loc[x,'dp+'] > 0.2):    
                print('dropped because large difference between mean and start dp+:',abs(mean-df.loc[x,'dp+'])/df.loc[x,'dp+'])
                continue
        except:
            print('Something went wrong in analysing found load, dropping ....')
            continue
#         print('hist:',df.hist(bins=10))
        
        # save this load to the distionairy (group by 'fingerprint')
        fingerprint = str(int(round(mean,-2)))+'_'#+str(int(left_round(df.loc[x,'dp+'],2)))
        temp = {'index':{'start':x,'stop':y},'time':time,'mean':mean,'max':max,'profile':profile}
        try:
            loads[fingerprint][len(loads[fingerprint])] = temp
        except:
            loads[fingerprint] = {0:temp}
            df[fingerprint] = 0 #add new colum to the dataframe before inserting found loads (only on first occurance!)
        
        df.loc[x:y-1,fingerprint] = profile[1:-1]
        df.loc[x:y-1,'unknown'] = df.loc[x:y-1,'unknown'] - profile[1:-1]
        print('Saved with fingerprint:',fingerprint)



 
start dp>100: 2017-09-21 19:32:09 start P: 173.0 dP+: 133.0
stop dP-: 2017-09-21 20:15:10 dP-: 120.0
149 409 230.33076923076922
mean load: 230.33076923076922
max load: 1071.0
std load: 285.376277743999
noise: 8.696153846153846
time past: 0 days 00:43:01
found profile from  2017-09-21 19:31:49 to 2017-09-21 20:15:10
[0.0, 133.0, 133.0, 179.0, 179.0, 180.0, 180.0, 181.0, 181.0, 179.0, 179.0, 179.0, 179.0, 169.0, 169.0, 170.0, 170.0, 168.0, 168.0, 168.0, 168.0, 167.0, 167.0, 167.0, 167.0, 168.0, 168.0, 167.0, 167.0, 172.0, 172.0, 173.0, 173.0, 173.0, 173.0, 160.0, 160.0, 160.0, 160.0, 161.0, 161.0, 155.0, 155.0, 154.0, 154.0, 152.0, 152.0, 149.0, 149.0, 161.0, 161.0, 969.0, 969.0, 970.0, 970.0, 1071.0, 1071.0, 1069.0, 1069.0, 1068.0, 1068.0, 1002.0, 1002.0, 1001.0, 1001.0, 996.0, 996.0, 990.0, 990.0, 989.0, 989.0, 990.0, 990.0, 992.0, 992.0, 988.0, 988.0, 983.0, 983.0, 982.0, 982.0, 174.0, 174.0, 174.0, 174.0, 174.0, 174.0, 173.0, 173.0, 175.0, 175.0, 175.0, 175.0, 175.0, 175.0, 175.0, 

stop dP-: 2017-09-22 04:08:22 dP-: 863.0
3253 3269 852.875
mean load: 852.875
max load: 868.0
std load: 11.99374837154757
noise: 55.0
time past: 0 days 00:02:39
found profile from  2017-09-22 04:05:23 to 2017-09-22 04:08:22
[0.0, 835.0, 835.0, 835.0, 835.0, 853.0, 853.0, 851.0, 851.0, 860.0, 860.0, 856.0, 856.0, 865.0, 865.0, 868.0, 868.0, 5.0]
Saved with fingerprint: 900_
 
start dp>100: 2017-09-22 04:10:01 start P: 238.0 dP+: 1802.0
stop dP-: 2017-09-22 04:10:41 dP-: 1794.0
3279 3283 1798.0
mean load: 1798.0
max load: 1802.0
std load: 4.618802153517006
noise: 452.5
time past: 0 days 00:00:40
found profile from  2017-09-22 04:09:41 to 2017-09-22 04:10:41
[0.0, 1802.0, 1802.0, 1794.0, 1794.0, 0.0]
Saved with fingerprint: 1800_
 
start dp>100: 2017-09-22 04:11:20 start P: 238.0 dP+: 1784.0
stop dP-: 2017-09-22 04:11:40 dP-: 1786.0
3287 3289 1784.0
mean load: 1784.0
max load: 1784.0
std load: 0.0
noise: 892.0
time past: 0 days 00:00:20
found profile from  2017-09-22 04:11:00 to 2017-09-2

stop demand: 2017-09-22 13:28:54 2.0  <=  2.0
6058 6130 88.83333333333333
mean load: 88.83333333333333
max load: 109.0
std load: 15.702336777743948
noise: 3.513888888888889
time past: 0 days 00:23:49
found profile from  2017-09-22 13:28:34 to 2017-09-22 13:52:43
[0.0, 107.0, 109.0, 107.0, 109.0, 106.0, 102.0, 99.0, 98.0, 94.0, 93.0, 91.0, 92.0, 90.0, 90.0, 89.0, 89.0, 89.0, 90.0, 89.0, 89.0, 88.0, 89.0, 90.0, 90.0, 90.0, 89.0, 89.0, 89.0, 89.0, 90.0, 90.0, 91.0, 90.0, 91.0, 91.0, 90.0, 91.0, 90.0, 89.0, 90.0, 90.0, 89.0, 90.0, 90.0, 90.0, 91.0, 91.0, 90.0, 90.0, 90.0, 89.0, 90.0, 89.0, 89.0, 88.0, 89.0, 89.0, 89.0, 90.0, 89.0, 88.0, 89.0, 88.0, 89.0, 89.0, 88.0, 88.0, 88.0, 88.0, 88.0, 2.0, 1.0, 0.0]
dropped because of large std: 0.17676176485265233
 
start dp>100: 2017-09-22 14:40:02 start P: 4.0 dP+: 108.0
stop demand: 2017-09-22 14:40:02 3.0  <=  4.0
6273 6343 90.01428571428572
mean load: 90.01428571428572
max load: 108.0
std load: 5.4573255039730455
noise: 2.2
time past: 0 days 00:

Saved with fingerprint: 2000_
 
start dp>100: 2017-09-22 20:22:49 start P: 10.0 dP+: 1529.0
stop dP-: 2017-09-22 20:23:09 dP-: 1402.0
7309 7310 1529.0
mean load: 1529.0
max load: 1529.0
std load: nan
noise: 1529.0
time past: 0 days 00:00:20
found profile from  2017-09-22 20:22:29 to 2017-09-22 20:23:09
[0.0, 1529.0, 127.0]
Saved with fingerprint: 1500_
 
start dp>100: 2017-09-22 21:30:59 start P: 32.0 dP+: 107.0
stop demand: 2017-09-22 21:30:59 4.0  <=  32.0
7515 7585 67.14285714285714
mean load: 67.14285714285714
max load: 110.0
std load: 13.551068960760851
noise: 2.7
time past: 0 days 00:23:10
found profile from  2017-09-22 21:30:39 to 2017-09-22 21:54:09
[0.0, 107.0, 110.0, 108.0, 109.0, 106.0, 105.0, 100.0, 74.0, 71.0, 71.0, 70.0, 70.0, 69.0, 67.0, 67.0, 63.0, 63.0, 63.0, 63.0, 62.0, 62.0, 64.0, 63.0, 64.0, 64.0, 63.0, 64.0, 63.0, 64.0, 63.0, 63.0, 62.0, 63.0, 63.0, 63.0, 62.0, 63.0, 62.0, 62.0, 63.0, 62.0, 62.0, 62.0, 62.0, 62.0, 62.0, 61.0, 61.0, 61.0, 61.0, 61.0, 61.0, 60.0, 62.

Saved with fingerprint: 1700_
 
start dp>100: 2017-09-23 07:47:46 start P: 13.0 dP+: 1781.0
stop dP-: 2017-09-23 07:48:06 dP-: 1780.0
9379 9380 1781.0
mean load: 1781.0
max load: 1781.0
std load: nan
noise: 1781.0
time past: 0 days 00:00:20
found profile from  2017-09-23 07:47:26 to 2017-09-23 07:48:06
[0.0, 1781.0, 1.0]
Saved with fingerprint: 1800_
 
start dp>100: 2017-09-23 07:48:26 start P: 14.0 dP+: 1779.0
stop dP-: 2017-09-23 07:48:46 dP-: 1779.0
9381 9382 1779.0
mean load: 1779.0
max load: 1779.0
std load: nan
noise: 1779.0
time past: 0 days 00:00:20
found profile from  2017-09-23 07:48:06 to 2017-09-23 07:48:46
[0.0, 1779.0, 0.0]
Saved with fingerprint: 1800_
 
start dp>100: 2017-09-23 07:49:25 start P: 14.0 dP+: 1687.0
stop dP-: 2017-09-23 07:49:45 dP-: 1687.0
9384 9385 1687.0
mean load: 1687.0
max load: 1687.0
std load: nan
noise: 1687.0
time past: 0 days 00:00:20
found profile from  2017-09-23 07:49:05 to 2017-09-23 07:49:45
[0.0, 1687.0, 0.0]
Saved with fingerprint: 1700_
 

...

dropped because of large std: 0.7034202252225543
 
start dp>100: 2017-09-26 21:36:30 start P: 213.0 dP+: 107.0
stop demand: 2017-09-26 21:36:30 148.0  <=  213.0
31563 31583 95.5
mean load: 95.5
max load: 112.0
std load: 20.387044389694363
noise: 15.75
time past: 0 days 00:03:19
found profile from  2017-09-26 21:36:21 to 2017-09-26 21:39:49
[0.0, 107.0, 111.0, 102.0, 112.0, 99.0, 102.0, 107.0, 106.0, 105.0, 106.0, 96.0, 95.0, 97.0, 87.0, 83.0, 93.0, 85.0, 91.0, 109.0, 17.0, -65.0]
dropped because of large std: 0.21347690460412946
 
start dp>100: 2017-09-26 22:47:58 start P: 4.0 dP+: 109.0
stop demand: 2017-09-26 22:47:58 4.0  <=  4.0
31995 32137 90.99295774647888
mean load: 90.99295774647888
max load: 110.0
std load: 9.163987857870328
noise: 2.119718309859155
time past: 0 days 00:23:30
found profile from  2017-09-26 22:47:48 to 2017-09-26 23:11:28
[0.0, 109.0, 109.0, 109.0, 110.0, 108.0, 109.0, 109.0, 108.0, 106.0, 106.0, 101.0, 100.0, 99.0, 99.0, 96.0, 95.0, 94.0, 93.0, 94.0, 94.0, 93.

36498 36646 87.91216216216216
mean load: 87.91216216216216
max load: 111.0
std load: 19.967636759071716
noise: 1.9527027027027026
time past: 0 days 00:24:29
found profile from  2017-09-27 11:12:50 to 2017-09-27 11:37:29
[0.0, 110.0, 110.0, 110.0, 109.0, 108.0, 111.0, 110.0, 109.0, 107.0, 106.0, 102.0, 101.0, 100.0, 99.0, 96.0, 95.0, 94.0, 94.0, 93.0, 93.0, 93.0, 93.0, 93.0, 92.0, 91.0, 91.0, 90.0, 90.0, 91.0, 90.0, 90.0, 90.0, 90.0, 91.0, 90.0, 91.0, 90.0, 89.0, 89.0, 89.0, 89.0, 89.0, 90.0, 90.0, 90.0, 90.0, 90.0, 90.0, 89.0, 90.0, 89.0, 90.0, 89.0, 90.0, 90.0, 90.0, 90.0, 91.0, 91.0, 91.0, 91.0, 90.0, 90.0, 91.0, 91.0, 91.0, 91.0, 91.0, 91.0, 92.0, 91.0, 91.0, 91.0, 91.0, 90.0, 90.0, 90.0, 90.0, 89.0, 92.0, 90.0, 90.0, 90.0, 90.0, 89.0, 90.0, 90.0, 90.0, 90.0, 89.0, 92.0, 91.0, 93.0, 92.0, 92.0, 92.0, 92.0, 92.0, 92.0, 92.0, 92.0, 92.0, 91.0, 91.0, 91.0, 92.0, 91.0, 90.0, 91.0, 91.0, 91.0, 90.0, 90.0, 90.0, 89.0, 91.0, 91.0, 91.0, 90.0, 90.0, 90.0, 91.0, 90.0, 90.0, 91.0, 90.0, 91.0,

found profile from  2017-09-27 16:18:25 to 2017-09-27 16:18:55
[0.0, 385.0, 389.0, -55.0]
Saved with fingerprint: 400_
 
start dp>100: 2017-09-27 16:19:05 start P: 1592.0 dP+: 413.0
stop dP-: 2017-09-27 16:19:55 dP-: 442.0
38348 38353 235.4
mean load: 235.4
max load: 453.0
std load: 212.61538044083264
noise: 251.0
time past: 0 days 00:00:50
found profile from  2017-09-27 16:18:55 to 2017-09-27 16:19:55
[0.0, 413.0, 286.0, 12.0, 13.0, 453.0, 11.0]
dropped because of large std: 0.9032089228582525
 
start dp>100: 2017-09-27 16:19:45 start P: 1605.0 dP+: 440.0
stop dP-: 2017-09-27 16:19:55 dP-: 442.0
38352 38353 440.0
mean load: 440.0
max load: 440.0
std load: nan
noise: 440.0
time past: 0 days 00:00:10
found profile from  2017-09-27 16:19:35 to 2017-09-27 16:19:55
[0.0, 440.0, -2.0]
Saved with fingerprint: 400_
 
start dp>100: 2017-09-27 16:20:14 start P: 1608.0 dP+: 438.0
stop dP-: 2017-09-27 16:20:34 dP-: 450.0
38355 38357 438.0
mean load: 438.0
max load: 438.0
std load: 0.0
noise: 219.

Saved with fingerprint: 1900_
 
start dp>100: 2017-09-27 20:27:45 start P: 129.0 dP+: 1969.0
stop dP-: 2017-09-27 20:37:31 dP-: 1962.0
39851 39910 1971.7288135593221
mean load: 1971.7288135593221
max load: 1985.0
std load: 9.721697220339198
noise: 36.0
time past: 0 days 00:09:46
found profile from  2017-09-27 20:27:35 to 2017-09-27 20:37:31
[0.0, 1969.0, 1963.0, 1964.0, 1965.0, 1980.0, 1981.0, 1983.0, 1983.0, 1982.0, 1982.0, 1985.0, 1979.0, 1982.0, 1980.0, 1978.0, 1982.0, 1982.0, 1980.0, 1980.0, 1981.0, 1980.0, 1981.0, 1979.0, 1981.0, 1981.0, 1979.0, 1974.0, 1976.0, 1974.0, 1975.0, 1975.0, 1970.0, 1974.0, 1974.0, 1977.0, 1981.0, 1977.0, 1980.0, 1977.0, 1973.0, 1958.0, 1958.0, 1956.0, 1955.0, 1958.0, 1953.0, 1960.0, 1957.0, 1958.0, 1957.0, 1957.0, 1957.0, 1964.0, 1963.0, 1964.0, 1964.0, 1961.0, 1967.0, 1966.0, 4.0]
Saved with fingerprint: 2000_
 
start dp>100: 2017-09-27 20:55:03 start P: 127.0 dP+: 108.0
stop demand: 2017-09-27 20:55:03 107.0  <=  127.0
40016 40207 79.50785340314137
me

Saved with fingerprint: 800_
 
start dp>100: 2017-09-28 05:27:16 start P: 23.0 dP+: 126.0
stop demand: 2017-09-28 05:27:16 4.0  <=  23.0
43112 43262 92.67333333333333
mean load: 92.67333333333333
max load: 141.0
std load: 14.016048647418462
noise: 2.5
time past: 0 days 00:24:49
found profile from  2017-09-28 05:27:06 to 2017-09-28 05:52:05
[0.0, 126.0, 111.0, 112.0, 111.0, 111.0, 111.0, 111.0, 111.0, 110.0, 108.0, 106.0, 103.0, 102.0, 100.0, 99.0, 97.0, 96.0, 96.0, 95.0, 95.0, 94.0, 94.0, 94.0, 94.0, 92.0, 92.0, 91.0, 91.0, 90.0, 91.0, 90.0, 90.0, 90.0, 90.0, 89.0, 90.0, 90.0, 90.0, 90.0, 90.0, 91.0, 90.0, 90.0, 91.0, 91.0, 91.0, 91.0, 90.0, 91.0, 90.0, 90.0, 90.0, 90.0, 90.0, 91.0, 91.0, 91.0, 91.0, 90.0, 91.0, 91.0, 91.0, 92.0, 91.0, 91.0, 92.0, 91.0, 92.0, 91.0, 92.0, 92.0, 90.0, 91.0, 91.0, 91.0, 91.0, 91.0, 105.0, 92.0, 93.0, 91.0, 91.0, 91.0, 91.0, 91.0, 140.0, 141.0, 141.0, 141.0, 140.0, 140.0, 140.0, 90.0, 90.0, 90.0, 91.0, 91.0, 89.0, 90.0, 90.0, 90.0, 90.0, 91.0, 90.0, 89.0, 

In [9]:
import plotly.offline
import plotly.graph_objs as go
import cufflinks
cufflinks.go_offline()

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [10]:
start = 0
points = 1000
try:
    start = plots * points
except:
    plots = 0
# plots = 0

    
res = df.set_index('datetime')
res[start:start+points].iplot(kind='line')

plots = plots +1
# df[].iplot()

In [11]:
# print(list(loads['100_'][0]))
for i in sorted(loads):
    print(i,'has',len(loads[i]),'occurance(s)')
#     for load in loads[i]:
#         if i == '100_':
#             print(round(sum(loads[i][load]['profile'])/360,1),'Wh in ',loads[i][load]['time'])
            


100_ has 85 occurance(s)
1300_ has 2 occurance(s)
1400_ has 1 occurance(s)
1500_ has 2 occurance(s)
1600_ has 7 occurance(s)
1700_ has 10 occurance(s)
1800_ has 6 occurance(s)
1900_ has 1 occurance(s)
2000_ has 7 occurance(s)
200_ has 8 occurance(s)
2100_ has 2 occurance(s)
2600_ has 1 occurance(s)
2700_ has 2 occurance(s)
2800_ has 1 occurance(s)
300_ has 7 occurance(s)
400_ has 13 occurance(s)
500_ has 2 occurance(s)
800_ has 11 occurance(s)
900_ has 3 occurance(s)


In [21]:
fingerprint = '100_'
max_length = 1;
for x in loads[fingerprint]:
    if max_length < len(loads[fingerprint][x]['profile']):
        max_length = len(loads[fingerprint][x]['profile'])
# print(list(range(1,max_length)))
profiles_data = pd.DataFrame(columns=list(loads[fingerprint]))
# print(profiles_data)
tempDF = pd.DataFrame(list(range(0,max_length)),columns=[x])

profiles_data = pd.concat([profiles_data,tempDF])

for x in loads[fingerprint]:
    l = len(loads[fingerprint][x]['profile'])
    profiles_data.loc[:l-1,x] = loads[fingerprint][x]['profile']
profiles_data.iplot(kind='line',filename='index.html')

In [20]:

res = df.set_index('datetime')
# res[:1000].iplot(kind='line')
# fig = res.plot()
# fig.show()
res.resample('15T').mean().iplot(kind='line',filename='index.html')



# res[:100]

In [19]:

# df[['datetime',list(loads)]].iplot()
temp = list(loads)
temp[0] = 'datetime'
temp[1] = 'baseload'
temp[2] = 'unknown'

temp[3:] =list(loads)
dp = df[temp]
dp = dp.set_index('datetime')
dp.resample('10T').mean().iplot(kind='line',filename='index.html')
# dp.resample('10T').mean().iplot(kind='area',fill='tozeroy',mode='none')



KeyError: "['100_'] not in index"

In [15]:
pie = dp.sum()
# values = pie.values/pie.sum()*100
round(pie/pie.sum()*100,1)


baseload    37.8
unknown     35.7
800_         2.9
100_         8.3
900_         0.9
1800_        0.4
300_         0.2
200_         0.1
2000_        5.7
1500_        0.0
1700_        0.4
1400_        0.5
1300_        0.7
2100_        3.3
400_         0.4
2700_        0.5
2600_        0.1
1600_        0.3
500_         0.1
2800_        1.0
1900_        0.8
dtype: float64

In [16]:
trace = go.Pie(labels=pie.index, values=pie.values)
dp.iplot([trace], filename='index.html')

In [17]:
# import plotly.plotly as py
import plotly.offline as py

trace = go.Pie(labels=pie.index, values=pie.values)

py.plot([trace], filename='disaggregator_results_pie.html');

# Try to rename colums for 'kwown loads' 

In [18]:
#relable output for known_loads
known_loads = {'100_':'Fridge','2000_':'Iron'}
for name in loads.keys():
    try:
        df=df.rename(columns = {name:known_loads[name]})
        loads[known_loads[name]] = loads[name]
    except:
        print(name,'not found known_loads')
    
for name in known_loads:
    try:
        del loads[name]
    except:
        print(name,'not found in legend')

legend = loads.keys()
print(list(legend))

800_ not found known_loads


RuntimeError: dictionary changed size during iteration

In [ ]:
import os.system

# php -t ~/Documents/GitHub/disaggregation/disaggregator-deltaPower/ -S 0.0.0.0:8000